# Exercice 1

L'idée de cet exercice était de vous faire classer des profils de notes d'utilisateurs Google Maps, posant la base d'un possible système de recommandation. On cherche le groupe auquel appartient un nouvel utilisateur (centre le plus proche dans le cas des k-means), puis on lui propose des attractions correspondant à ses "profils voisins".

L'idée est donc plutôt de sélectionner les $k$ plus proches voisins du nouveau point avant de les utiliser pour guider les suggestions. Cependant, avoir réalisé un clustering préliminaire permet de rechercher les voisins dans un groupe réduit, accélérant les calculs. La réactivité des applis web est en effet un facteur important.

Un affichage des premières lignes du jeu de données montre qu'il n'y a en fait pas de "colonne 26", chaque ligne se terminant par une virgule :

$ head google_review_ratings.csv
User,Category 1,Category 2,Category 3,Category 4,Category 5,Category 6,Category 7,Category 8,Category 9,Category 10,Category 11,Category 12,Category 13,Category 14,Category 15,Category 16,Category 17,Category 18,Category 19,Category 20,Category 21,Category 22,Category 23,Category 24, <br>
User 1,0,0,3.63,3.65,5,2.92,5,2.35,2.33,2.64,1.7,1.69,1.7,1.72,1.74,0.59,0.5,0,0.5,0,0,0,0,0, <br>
User 2,0,0,3.63,3.65,5,2.92,5,2.64,2.33,2.65,1.7,1.69,1.7,1.72,1.74,0.59,0.5,0,0.5,0,0,0,0,0, <br>
User 3,0,0,3.63,3.63,5,2.92,5,2.64,2.33,2.64,1.7,1.69,1.7,1.72,1.74,0.59,0.5,0,0.5,0,0,0,0,0, <br>
User 4,0,0.5,3.63,3.63,5,2.92,5,2.35,2.33,2.64,1.73,1.69,1.7,1.72,1.74,0.59,0.5,0,0.5,0,0,0,0,0, <br>
User 5,0,0,3.63,3.63,5,2.92,5,2.64,2.33,2.64,1.7,1.69,1.7,1.72,1.74,0.59,0.5,0,0.5,0,0,0,0,0, <br>
User 6,0,0,3.63,3.63,5,2.92,5,2.63,2.33,2.65,1.71,1.69,1.69,1.72,1.74,0.59,0.5,0,0.5,0,0,0,0,0, <br>
User 7,0,5,3.63,3.63,5,2.92,3.03,2.35,2.33,2.64,1.73,1.68,1.69,1.71,1.75,0.59,0.5,0,0.5,0,0,0,0,0, <br>
User 8,0,5,3.63,3.63,5,2.92,5,2.63,2.33,2.64,1.7,1.68,1.69,1.71,1.74,0.6,0.5,0,0.5,0,0,0,0,0, <br>
User 9,0,5,3.64,3.64,5,2.92,3.03,2.62,2.32,2.63,1.71,1.67,1.68,1.7,0.75,0.6,0,0,0.5,0,0,0,0,0,

R lit une 26eme colonne à cause de cette virgule, mais elle ne peut contenir que des NA. On se contentera des 25 premières :)

In [ ]:
data <- read.csv("../data/google_review_ratings.csv")
data <- data[,-ncol(data)]
dim(data)
head(data)

La première colonne contient un identifiant d'utilisateur anonymisé : on la supprime, celle-ci n'offrant aucune information utile.

In [ ]:
data <- data[,-1]

Assurons-nous ensuite que toutes les colonnes soient bien numériques :

In [ ]:
for (i in seq_len(ncol(data))) print(paste(i, class(data[,i])))

Tiens donc... un "character" parmi les "numeric" ! Pourquoi ? Let's see...

In [ ]:
# Recherche d'une chaîne non conforme.
# Pas besoin de tenir compte d'éventuels exposants : on sait que les notes sont entre 0 et 5.
grep("^[0-9]+.?[0-9]*$", data[,11], invert=TRUE)

In [ ]:
data[2713,11]

Bizarre... une tabulation a sans doute remplacé une virgule par erreur. Dans le doute, supprimons cette ligne.

In [ ]:
data <- data[-2713,]
data[,11] <- as.double(data[,11])

Maintenant data est full numeric, mais peut encore comporter des valeurs manquantes.

In [ ]:
#data[which(!complete.cases(data)),] #montre la ligne où category24 manque
data <- na.omit(data)

L'extrait des 6 premières lignes ci-dessus semble indiquer que les premiers individus sont identiques, et donc qu'il pourrait y avoir pas mal de redondances dans ces données. Vérifions :

In [ ]:
as.matrix(dist(data[1:6,]))

In [ ]:
data[1:2,which(data[1,] != data[2,])]

Ok, l'impression visuelle était fausse. Les premiers individus au moins sont cependant identiques sur les 22 catégories restantes.

Après cette analyse préliminaire, on est paré pour lancer les algorithmes :

In [ ]:
# Je ne sais pas quelle valeur choisir pour k, alors profitant du fait que le k-means est rapide, balayons :
library(clusterCrit)
mdata <- as.matrix(data) #nécessaire pour clusterCrit
silhouette <- c()
for (k in 2:20) {
    km <- kmeans(mdata, k, nstart=5)
    silhouette <- c(silhouette, intCriteria(mdata, km$cluster, "Silhouette")$silhouette)
}

In [ ]:
options(repr.plot.width=15, repr.plot.height=10)
plot(silhouette, type="l")
(2:20)[which.max(silhouette)]

Le critère silhouette étant maximal pour $k=7$, on peut se dire ok, il y a plutôt 7 groupes.
**Attention** cependant, ce critère vaut 1 à la limite (un point = un groupe). La comparaison n'a de sens que si on se limite à de petites valeurs de $k$.

Note : on trouve sur le web le critère qu'on vient de calculer, "The optimal number of clusters k is the one that maximize the average silhouette over a range of possible values for k" https://www.datanovia.com/en/lessons/cluster-validation-statistics-must-know-methods/ , et divers autres. La "Elbow method" qui cherche un coude dans le graphe d'évolution de l'inertie intra et la "Gap statistic" https://hastie.su.domains/Papers/gap.pdf sont classiques.

In [ ]:
# Juste pour indiquer que factoextra implémente les trois méthodes précitées :
#library(factoextra)
#fviz_nbclust(data, kmeans, method = "wss")
#fviz_nbclust(data, kmeans, method = "silhouette")
#fviz_nbclust(data, kmeans, method = "gap_stat")

# Voir aussi le package NbClust référencé sur dananovia.com

Tentative de visualisation des 7 clusters. Pas évident : dimension 24 !

In [ ]:
km <- kmeans(mdata, 7, nstart=5)
library(factoextra)
fviz_cluster(km, data=data)

Alors certes on ne voit pas grand chose, mais ce qui est intéressant puisqu'on a choisi les k-means, c'est de regarder les centroïdes :

In [ ]:
km$centers
matplot(t(km$centers), type="l", lty=1, lwd=2, col=rainbow(7))

On voit bien apparaître des profils différents : en ordonnées les notes, en abscisses les catégories, en 7 couleurs arc-en-ciel (pourquoi pas), les 7 centres.

Ensuite l'exercice demandait de comparer avec des distances de graphe : on voit assez mal l'intérêt dans ce cas, mais essayons.

In [ ]:
library(nngd)
o <- nng(data, k=20, mutual=TRUE) #attention k = nombre de voisins ici
dists_graph <- igraph::distances(o$graph, weights=o$distances)

In [ ]:
library(cluster)
# pamonce=1 permet de diminuer le temps d'exécution ; cf. aide ?pam
p <- pam(as.dist(dists_graph), k=7, pamonce=1)

In [ ]:
fviz_cluster(list(data=data, cluster=p$clustering))

Un cluster regroupe la quasi totalité des observations... Phénomène étonnant qu'il faut expliquer.

In [ ]:
range(dists_graph)
# ...Ok on tient l'explication ! Graphe probablement non connexe.
igraph::count_components(o$graph)
# 86 composantes connexes => on voit juste les 6 les plus denses ici.

Augmentons la taille des voisinages jusqu'à rendre le graphe connexe :

In [ ]:
k = 100
o <- nng(data, k=k, mutual=TRUE)
igraph::count_components(o$graph) #3

In [ ]:
k = 150
o <- nng(data, k=k, mutual=TRUE)
igraph::count_components(o$graph) #2

In [ ]:
k = 200
o <- nng(data, k=k, mutual=TRUE)
igraph::count_components(o$graph) #1 !

In [ ]:
dists_graph <- igraph::distances(o$graph, weights=o$distances)
p <- pam(as.dist(dists_graph), k=7, pamonce=1)

In [ ]:
fviz_cluster(list(data=data, cluster=p$clustering))

L'allure du graphe résultat est la même que pour les k-means. Regardons les médoïdes :

In [ ]:
data[p$medoids,]
extCriteria(km$cluster, p$clustering, "Rand")
matplot(t(data[p$medoids,]), type="l", lty=1, lwd=2, col=rainbow(7))

Conclusion : les partitions sont semblables.

Aucune bonne note dans les centroïdes aux alentours des clusters 16 à 20 : cela signifie que ces catégories ne sont pas très discriminantes - faible variabilité, peut-être. Sans entrer dans les détails, regardons à quoi elles correspondent :

Attribute 15 : Average ratings on juice bars <br>
Attribute 16 : Average ratings on art galleries <br>
Attribute 17 : Average ratings on dance clubs <br>
Attribute 18 : Average ratings on swimming pools <br>
Attribute 19 : Average ratings on gyms <br>
(Attention au décalage : on a supprimé la colonne 1 donc 15 --> 16 etc).

# Exercice 2

L'objectif de cet exercice est cette fois d'étudier la topologie du réseau aérien. On peut imaginer une application simple : étant donné la position d'un utilisateur, l'onglet "vol locaux" n'afficherait que les trajets dans son cluster, par exemple. On peut aussi songer à évaluer le degré de connexion entre différentes zones.

Il serait sans doute plus intéressant d'étudier l'impact de l'ajout ou suppression d'un aéroport en un point précis, mais cela nécessiterait plus d'informations : fréquence des vols, et taux de remplissage des avions, au moins.

TODO...